In [ ]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from matplotlib import cm
from PIL import Image
import glob
import os
from sklearn.model_selection import train_test_split
from sklearn.metrics import jaccard_score,log_loss, mean_absolute_error,median_absolute_error, mean_squared_error
%matplotlib inline
from tqdm import tqdm
import pickle
def makefile(what,filename):
    with open(filename,"wb") as f3:
        pickle.dump(what,f3)

def readfile(filename):
    with open(filename,"rb") as f4:
        ans=pickle.load(f4)
    return ans
from sklearn.mixture import GaussianMixture
from sklearn.cluster import KMeans
from sklearn.linear_model import LinearRegression
from sklearn.metrics import jaccard_score,log_loss, mean_absolute_error,median_absolute_error, mean_squared_error
from sklearn.metrics import roc_auc_score
from sklearn.naive_bayes import CategoricalNB
import warnings
warnings.filterwarnings('ignore')
from sklearn.metrics import accuracy_score
from sklearn.metrics import balanced_accuracy_score
import sys
import os

# AUC score

In [ ]:
result2=[]
K=25
kmeans=KMeans(n_clusters=K,max_iter=30)
dim=2
for e in range(5):
    train=readfile("X.pickle")
    train_label=readfile("y.pickle")
    train, x_test, train_label, y_test = train_test_split(train, train_label, test_size=0.2, random_state=e)
    result1=[]
    for i in range(20):
        print(i)
        x_train=train[train_label==i]
        y_label=np.zeros(len(y_test))
        y_label[y_test==i]=1
        training_data=np.array([np.array([np.array(x_train[j,n:n+dim]) for n in range(len(x_train[0])-(dim-1))]) for j in range(len(x_train))])
        training_data=training_data.reshape(training_data.shape[0]*training_data.shape[1],training_data.shape[2])
        
        kmeans.fit(training_data)
        result=kmeans.predict(training_data)
        CB=np.zeros(K)
        
        for cluster in result:
            CB[cluster]+=1
        LP=CB/len(result)*659
        testing_data=np.array([np.array([np.array(x_test[j,n:n+dim]) for n in range(len(x_test[0])-(dim-1))]) for j in range(len(x_test))])
        LCB_list=[]
        for each in testing_data:
            cluster_test=kmeans.predict(each)
            LCB=np.zeros(K)
            for cluster in cluster_test:
                LCB[cluster]+=1
            LCB_list.append(LCB)
        
        unseen_score=abs(np.array(LCB_list)-LP).sum(axis=1)
            
        AUC=roc_auc_score(y_label,-unseen_score)
        result1.append(AUC)
    result2.append(result1)
        
        
    

In [30]:
result2

[[0.9070476079073576,
  0.7949731857197688,
  0.7134607464882431,
  0.8450239002181217,
  0.8752301113672749,
  0.8506402087000502,
  0.7962026132101772,
  0.6541160017607515,
  0.8356517663261384,
  0.9563411061887059,
  0.9935222411508613,
  0.8223589815726544,
  0.804800376319901,
  0.8938258112947439,
  0.8424713794342625,
  0.6253194046587163,
  0.903691929591863,
  0.7469711449588259,
  0.8381088894057136,
  0.8211360326980192],
 [0.922146675672123,
  0.8076274373327967,
  0.715256548867288,
  0.848619932341685,
  0.8883230283266443,
  0.849794142614601,
  0.7949016370890081,
  0.66409439293485,
  0.8356324130972018,
  0.9546055267573186,
  0.9892984628833685,
  0.8365489298527775,
  0.7981627742286809,
  0.8803534373926797,
  0.8496218105222846,
  0.6188905668810012,
  0.8965074398273505,
  0.7379359608591429,
  0.8251457093092781,
  0.8107475530189256],
 [0.9161027568044111,
  0.7993788833826838,
  0.7242270564610206,
  0.8453346392451904,
  0.8803486036512898,
  0.856941075928

In [36]:
a=np.array(result2).mean(axis=0)*100
b=np.array(result2).std(axis=0)*100

In [40]:
for i in range(len(a)):
    print(str(np.round(a[i],1))+"±"+str(np.round(b[i],1)))
print(np.round(a.mean(),1))

91.7±0.6
80.0±0.5
72.0±0.5
85.0±0.6
88.1±0.5
85.4±0.3
81.1±1.5
64.3±2.1
83.1±0.5
95.6±0.1
99.2±0.2
82.5±0.9
79.9±0.3
89.1±0.5
84.7±0.8
62.4±1.0
90.4±0.4
73.9±0.7
83.0±0.8
82.3±0.9
82.7


# Processing time

In [41]:
K=25
kmeans=KMeans(n_clusters=K,max_iter=30)
dim=2
e=0
i=0
train=readfile("X.pickle")
train_label=readfile("y.pickle")
train, x_test, train_label, y_test = train_test_split(train, train_label, test_size=0.2, random_state=e)
x_train=train[train_label==i]
y_label=np.zeros(len(y_test))
y_label[y_test==i]=1

In [42]:
%%time
training_data=np.array([np.array([np.array(x_train[j,n:n+dim]) for n in range(len(x_train[0])-(dim-1))]) for j in range(len(x_train))])
training_data=training_data.reshape(training_data.shape[0]*training_data.shape[1],training_data.shape[2])

kmeans.fit(training_data)
result=kmeans.predict(training_data)
CB=np.zeros(K)

for cluster in result:
    CB[cluster]+=1
LP=CB/len(result)*659

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c212eee0>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c212e4c0>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'


CPU times: user 1min 26s, sys: 2min 23s, total: 3min 50s
Wall time: 16.3 s


In [44]:
%%time
testing_data=np.array([np.array([np.array(x_test[j,n:n+dim]) for n in range(len(x_test[0])-(dim-1))]) for j in range(len(x_test))])
LCB_list=[]
for each in testing_data:
    cluster_test=kmeans.predict(each)
    LCB=np.zeros(K)
    for cluster in cluster_test:
        LCB[cluster]+=1
    LCB_list.append(LCB)

unseen_score=abs(np.array(LCB_list)-LP).sum(axis=1)

AUC=roc_auc_score(y_label,-unseen_score)

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c212ee50>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94f4f68c10>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94f4f68c10>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94f4f68c10>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/t

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94f4f68c10>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

...

Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c84a8310>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/thre

    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c84a8a60>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packag

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c84a84c0>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'
Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_i

Exception ignored on calling ctypes callback function: <function _ThreadpoolInfo._find_modules_with_dl_iterate_phdr.<locals>.match_module_callback at 0x7f94c84a84c0>
Traceback (most recent call last):
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 400, in match_module_callback
    self._make_module_from_path(filepath)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 515, in _make_module_from_path
    module = module_class(filepath, prefix, user_api, internal_api)
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 606, in __init__
    self.version = self.get_version()
  File "/home/toshihayashi/anaconda3/lib/python3.8/site-packages/threadpoolctl.py", line 646, in get_version
    config = get_config().split()
AttributeError: 'NoneType' object has no attribute 'split'


CPU times: user 14min 4s, sys: 6.38 s, total: 14min 10s
Wall time: 1min 2s
